# NCRM Text Data Workshop - part 2: Scraping web pages
#### Lewys Brace - l.brace@exeter.ac.uk

### 1. Collecting textual data
Before you can do any textual data analysis, you first need a data set containing text data to work with. Finding an appropriate data set is often the hardest part of a text data project. There are, however, a number of ways in which you can gain access to data.

1. <b>Finding a dataset that has already been collected</b>. Without a doubt this is easiest option, but you are limited to what others have already collected (I'll point you to datasets from my own research that you are free to use for your project).
2. <b>Find and use an API</b>. There are hundreds (if not thousands!) of APIs on the web that provide textual data in some way shape or form. These include relatively open social media APIs (such as tweepy for Twitter), partially open APIs such as Google News (https://newsapi.org/s/google-news-api), and paid services such as webhose (https://webhose.io).
3. <b>Find a UoE database</b> with textual data. The obvious candidates are <a href="https://libguides.exeter.ac.uk/az.php?a=n">Nexus UK</a> and <a href="https://libguides.exeter.ac.uk/az.php?a=p">Proquest News and Newspapers</a>.
4. <b>Scrape your own data</b>! This is the most versatile solution, but also has the steepest learning curve.

This part of the workshop is going to focus on this last option. There are many different options for web scraping in Python. Here, we will be using the ``requests`` library to communicate (or send requests) to a web server and the ``lxml`` module to parse the returned HTML. As covered in part one, the first thing we need to do here is to do is import the necessary dependencies:

In [ ]:
import requests
from lxml import html

We can then use the ``requests`` in order to communicate with a website URL and get the content from it.

In [ ]:
url = "https://socialsciences.exeter.ac.uk/sociology/staff/"
page = requests.get(url)

The ``page`` object is an example of a ``class`` object, which we covered in the last video. These ``class`` objects have a number of ``methods``, which allow us to interact with it. There are numerous arguments that allow you to carry out specific tasks; i.e. we can view the raw HTML content by specifying the ``content`` argument:

In [ ]:
print(page.content[0:300])

We now want to parse the raw HTML that we collected with the ``requests`` package into a format that will make it easy to navigate. We can do this by building a tree using the ``lxml`` module that we imported above. This essentially simulates a web browser in which you open a URL. Just as your browser requests information from a web server and organizes into a tree, the ``requests`` library communicates with the server and returns the HTML, while the ``lxml`` package organises it into a tree:

In [ ]:
tree = html.fromstring(page.content)
print(tree)

Similar to the ``page`` object, the ``tree`` object has a bunch of methods that allow us to search for elements in a web page that we want to extract. Perhaps the most useful method to navigate the page's HTML tree is the XPath.

### 2. XPaths

It is worth spending some time familiarising ourselves with XPaths before we carry on building our web scraper. XPaths are a way of navigating our tree, and can be thought of as an address to a specific element(s) on a web page. As an example. let's say that we wanted to extract the text from the "Our research" menu option on the Exeter SPA's staff page. We can select this object by copying its Xpath from Chrome:

In [ ]:
print(tree.xpath('//*[@id="main-menu"]/div[2]/ul/li[4]/a/text()'))

As another example, we can use use our web browser to easily get the XPaths to a specific staff member's profile:

In [ ]:
print(tree.xpath('//*[@id="left-col"]/table[2]/tbody/tr[3]/td[1]/a'))

What if we wanted to get the URL of my staff profile? Well, we can just add the ``href`` attribute from the ``a`` tag.

In [ ]:
print(tree.xpath('//*[@id="left-col"]/table[2]/tbody/tr[3]/td[1]/a/@href'))

Then, we can combine this with the base URL for the staff page in order to get the full URL for my staff profile page:

In [ ]:
print(url + tree.xpath('//*[@id="left-col"]/table[2]/tbody/tr[3]/td[1]/a/@href')[0])

### 3. Other XPath expressions
There are a bunch of other XPath expressions that could prove useful in the future. We'll take a quick look at some of the most commonly used ones.

#### Contains
The ``contains`` expression is useful to only select elements that "contain" certain text, ids, classes. As an example, let's pretend I wanted to look for my colleague Chris:

In [ ]:
# Look up any <a> tags that include "Chris"
chris = tree.xpath('//a[contains(., "Chris")]')
print(chris)
print('Number of links with Chris = %s' % len(chris))
#The Chris I need is in location two in the returned list.
print(chris[1].text_content())

#### XPath operators

When using XPaths, you can also make use of a number of standard operators. These operators include:

* ``=`` Equivalent comparison, can be used for numeric or text values
* ``!=`` Is not equivalent comparison
* ``>``, ``>=`` Greater than, greater than or equal to
* ``<``, ``<=`` Less than, less than or equal to
* ``or`` Boolean or
* ``and`` Boolean and
* ``not`` Boolean not

For example, say we wanted to select the links that do <b>not</b> have "Lewys" in the text:



In [ ]:
print('The total number of links on the page = %s' % len(tree.xpath('//a')))

# Find links without "Lewys"
no_lewys = tree.xpath('//a[not(contains(., "Lewys"))]')

print('Number of links without a "Lewys" = %s' % len(no_lewys))

As another example, say we wanted all of the "Chris", except for "Chris Playford":

In [ ]:
no_playford = tree.xpath('//a[contains(., "Chris") and not(contains(., "Playford"))]')
print(len(no_playford))

### 4. Other useful ``lxml`` methods

In addition to `xpath`, `lxml.html` objects have a number of other useful methods. We already used the `text_content()` method, which simply returns the text of an HTML object. Here are some other methods that could come in handy.

#### `cssselect()`

In addition to using Xpaths to select objects, you can also use CSS (Cascading style sheets). As an example:

In [ ]:
import cssselect
nav = tree.cssselect('#main-menu')
print(nav[0].text_content())

#### find_class()

In [ ]:
plist = tree.find_class('profile_list')
print(plist)
print(plist[0].text_content())

#### get_element_by_id()

In [ ]:
nav = tree.get_element_by_id('main-menu')
print(nav.text_content())

### 5. Scraping our first page(s)

Okay, so let's start scraping our web pages. The aim of this exercise is to work out how many staff members in the University of Exeter's SPA department are interested in quantiative methods. As such, we need to start by getting the textual data from the SPA staff pages. We'll break the scraping task into two steps: 1) getting the links to each staff member's profile and 2) extracting the profile content.

By inspecting the page source in our browser, we see that the information that we want (staff member name, a link to their page, and their title) is located in 6 "profile_list" tables in the "main-content" div. Let's start by extracting all of the "rows" from these tables:

In [ ]:
# XPath to extract all of the rows in all of the
# in "profile_list" tables
table = tree.xpath('//*[@class="profile_list"]//tr')

# How many rows do we have?
print(len(table))
print(table[0])

If you look closely at the "profile_list" tables, you'll notice that these tables include a header at the top (e.g., "Head of Department") and these headers will now be "sprinkeled" through our `tables` object. 

In [ ]:
table[1].text_content()

So we are going to need to deal with this issue. Also, notice that the information that we actually want is located in a <tr> tag and that the header rows don't have these tags.

In [ ]:
# Look for the <td> tag in a header row
header = table[0].findall('./td')
print(header)

# And compare this to a non-header row
non_header = table[1].findall('./td')
print(non_header)

# We can also look at the text in these "Element td"
# objects
print(non_header[0].text_content())
print(non_header[1].text_content())

The above code illustrates something quite useful: we can use the `findall()` method to look for an XPath <i>within</i> another XPath. Here, we asked `lxml` to "findall" of the <td> tags -- i.e., both cells in the table for that row.

OK, so we are already most of the way there -- the only thing remaining is to extract the profile link for each member of staff. Again, if you look at the source in your browser, you will see that the URL to each staff member's profile is located in the cell holding their name. Let's grab this for Prof. Michael:

In [ ]:
print(non_header[0].find('./a').attrib['href'])

Here, we use find to find only the first "a" tag (as opposed to findall which could give more than 1) and ask for the href attribute. Sweet -- now we really have everything that we need. Only thing remaining is to pull everything together and loop over each row in the table, extract the information that we need, and save it:

In [ ]:
# Get the table rows
table = tree.xpath('//*[@id="main-content"]//tr')

# Extract name, staff page URL, and position
# of each staff member
staff_profiles = []

for row in table:
    # Get the cells of the HTML table
    cells = row.findall('./td')
    # Headers in the table do not have a td tag.
    # We will ignore these.
    if len(cells) != 0:
        # Get the URL to the staff member's webpage
        page_url = cells[0].find('./a')
        if page_url is not None:
            page_url = cells[0].find('./a').attrib['href']
        staff_profiles.append({'name': cells[0].text_content(),
                               'page_url': page_url,
                               'position': cells[1].text_content()})

print("Extracted information for %s members of staff." % len(staff_profiles))

In [ ]:
print(staff_profiles[3])

For our second step,need to extract the content of the profiles. Here, we have our profile URLs and a bit of useful meta data (name and position). The next step is to loop over the `staff_profile` list, visit the profile page, and extract the content. Let's take one step at a time. We start by visiting a webpage in the usual way:

In [ ]:
page = requests.get(url + staff_profiles[0]['page_url'])
print("We extracted the following page:\n%s" % page.url)
# And build the tree in the usual way:
tree = html.fromstring(page.content)

After looking at the page, the profile content is located in paragraphs (``<p>``) in the various divs in the ``class = "tab-content clear-fix"`` div. For instance, if we wanted to pull the "overview" text:

In [ ]:
# Extract all overview content located in paragraph tags
overview = '\n\n'.join([p.text_content().strip() for p in 
                       tree.xpath('//*[@id="overview"]//p')]).strip()

print(overview)

We can also pull other aspects of Mike's page:

In [ ]:
# Extract all research content located in paragraph tags
research = '\n\n'.join([p.text_content().strip() for p in 
                       tree.xpath('//*[@id="research"]//p')]).strip()

print(research)

Or we can just grab everything in at once:

In [ ]:
# Extract all content located in paragraph tags
content = '\n\n'.join([p.text_content().strip() for p in 
                       tree.xpath('//*[@id="main-content"]//p')]).strip()

print(content)

We'll keep things simple and use all available page content moving forward. The last step is to loop over the entire staff_profile list and get the profile content for each person:

In [ ]:
# Extract page text
for staff in staff_profiles:
    # Visit staff member landing page
    page = requests.get(url + staff['page_url'])
    
    # Parse the xml tree. We will ignore any unicode errors for the
    # moment.
    tree = html.fromstring(page.content.decode('utf-8', errors='ignore'))
    
    # Extract all content located in paragraph tags
    content = '\n\n'.join([p.text_content().strip() for p in 
                           tree.xpath('//*[@id="main-content"]//p')])
    
    # Add text content to dictionary
    staff['page_content'] = content

We added add additional field in our staff_profiles list of dictionaries and we can call this information in the usual way:

In [ ]:
print(staff_profiles[3]['page_content'])

With the page content in hand, we are in a position to offer a preliminary to our research question. Here, we'll keep things really simple. Let's look up the staff that have the word "statistic" or "quant" in their profile page:

In [ ]:
quantitative = []

for row in staff_profiles:
    if 'page_content' in row:
        if ('quant' in row['page_content']) or ('statistic' in row['page_content']):
            quantitative.append(row)

print('Found %s staff members that reference quantitative work:' % len(quantitative))

for row in quantitative: 
    print(row['name'])

Now we saave our profiles to an output file.

In [ ]:
import json
with open('C:/Users/lb690/OneDrive - University of Exeter/Teaching/NLP_workshop/profiles.json', 'w') as jfile:
    json.dump(staff_profiles, jfile, indent=4, separators=(',', ': '), sort_keys=True)
    # Add trailing newline for POSIX compatibility
    jfile.write('\n')